# Import libraries

In [1]:
import os
import warnings

import numpy as np
import pandas as pd

import matplotlib.pyplot as plt
import matplotlib.ticker as ticker
import matplotlib.cm as cm

import seaborn as sns

import re

from scipy.signal import find_peaks

from collections import defaultdict

from tqdm import tqdm

In [2]:
warnings.filterwarnings("ignore")

pd.set_option('display.max_columns', 50)
pd.set_option('display.max_rows', 100)
pd.set_option('display.max_colwidth', None)

In [3]:
path_to_save = './../results/03a_features'

# Loading data

In [4]:
path_to_ftir_data= './../data/preprocessed_data/scaled_data'
path_to_samples_description = './../data/parsed_data/samples_description.csv'

## FTIR-spectra

In [5]:
files = os.listdir(path_to_ftir_data)

In [6]:
data_ranges = {}

for file in files:
    startswith_ftir_flg = file.startswith("ftir")

    if not startswith_ftir_flg:
        continue
    
    high_boundary = int(file.split('_')[-2])
    low_boundary = int(file.split('_')[-1].split('.')[0])

    wn_range = (high_boundary, low_boundary)
    tmp_data = pd.read_csv(f'{path_to_ftir_data}/{file}', sep=';', index_col=0)
    tmp_data.columns = tmp_data.columns.astype(float)

    data_ranges[wn_range] = tmp_data

    print(
        f'-' * 224,
        f'WAVENUMBER RANGE: {wn_range}',
        f'(*) data set shape: {data_ranges[wn_range].shape}',
        f'(*) Wavenumber for data (max/min): {round(data_ranges[wn_range].columns.max()), round(data_ranges[wn_range].columns.min())}',
        sep='\n'
    )

--------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------
WAVENUMBER RANGE: (1800, 1500)
(*) data set shape: (75, 311)
(*) Wavenumber for data (max/min): (1800, 1501)
--------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------
WAVENUMBER RANGE: (1500, 1300)
(*) data set shape: (75, 207)
(*) Wavenumber for data (max/min): (1500, 1301)
--------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------
WAVENUMBER RANGE: (3800, 2500)
(*) data set shape: (75, 1348)
(*) Wavenumber for data (max/min): (3800, 250

## Samples description

In [7]:
samples_description = pd.read_csv(f'{path_to_samples_description}', sep=';', index_col=0)

print(samples_description.shape)
samples_description.head(3)

(75, 6)


Row_ID  Division  Size Fraction_hue  \
division_1_size_bulk       1         1  bulk        $> 0$   
division_1_size_5          2         1     5        $< 5$   
division_1_size_3          3         1     3        $< 3$   

                     Fraction_grouped_hue  Class  
division_1_size_bulk              $d > 5$      2  
division_1_size_5          $2 < d \leq 5$      1  
division_1_size_3          $2 < d \leq 5$      1

# Feature extraction

## Base parameters

In [8]:
hue = samples_description['Fraction_grouped_hue'].tolist()
target = samples_description['Class'].tolist()

In [9]:
type_color_dict = {
    '$d \leq 2$': '#2166AC',
    '$2 < d \leq 5$': '#67A9CF',
    '$d > 5$': '#B2182B'
}

In [10]:
groups = list(type_color_dict.keys())

In [11]:
sns.set_theme()

## Spectral peaks extraction

### Function for peaks calculation

In [12]:
def find_spectrum_peaks(wavenumber, spectrum, prominence=0.03, height=0.05, width=10):
    peaks, properties = find_peaks(
        spectrum,
        prominence=prominence,
        height=height,
        width=width
    )
    
    peak_positions = wavenumber[peaks]
    peak_intensities = spectrum[peaks]
    
    return peak_positions, peak_intensities, properties

### Function for specra with peaks visualization

In [13]:
def visualize_grouped_spectra(grouped_data, peak_data, groups, type_color_dict=None, plot_style=None, plot_params=None, path_to_save=None):
    
    if type_color_dict is None:
        type_color_dict = {group: 'blue' for group in groups}

    if plot_style is None:
        plot_style = {
            "LINEWIDTH": 3.5,
            "PEAK_SIZE": 64,
            "PEAK_COLOR": "red",
            "TITLE_FONTSIZE": 20,
            "X_LABEL_FONT_SIZE": 16,
            "Y_LABEL_FONT_SIZE": 16,
            "X_LABELPAD": 5,
            "Y_LABELPAD": 15,
            "TICK_FONTSIZE": 14,
            "X_NBINS": 10,
            "Y_NBINS": 12
        }

    if plot_params is None:
        plot_params = {
            "FIGSIZE_SCALE": (6, 3),
            "X_LABEL": 'Волновое число, см$^{-1}$',
            "Y_LABEL": '$A_{n}$'
        }

    ncols = len(groups)
    nrows = max([len(grouped_data[group]) for group in groups])
    figsize = (ncols * plot_params["FIGSIZE_SCALE"][0], nrows * plot_params["FIGSIZE_SCALE"][1])

    fig, axes = plt.subplots(nrows=nrows, ncols=ncols, figsize=figsize, dpi=300)
    axes = np.array([axes]) if nrows == 1 else axes.reshape(nrows, ncols)

    for col, group in tqdm(enumerate(groups)):
        group_data = grouped_data[group]
        color = type_color_dict.get(group, 'blue')

        for row, sample_id in enumerate(group_data.index):
            ax = axes[row, col]
            spectrum = group_data.loc[sample_id].values
            wavenumber = group_data.columns.astype(float)

            ax.plot(wavenumber, spectrum, color=color, linewidth=plot_style["LINEWIDTH"])

            peaks = peak_data.get(sample_id, {})
            peak_positions = peaks.get("positions", [])
            peak_intensities = peaks.get("intensities", [])

            ax.scatter(peak_positions, peak_intensities, s=plot_style["PEAK_SIZE"],
                       color=plot_style["PEAK_COLOR"], marker='o')

            if row == 0:
                ax.set_title(f'{group}', fontsize=plot_style["TITLE_FONTSIZE"], fontstyle='italic')

            ax.set_xlabel(plot_params["X_LABEL"], fontsize=plot_style["X_LABEL_FONT_SIZE"], labelpad=plot_style["X_LABELPAD"])
            ax.set_ylabel(plot_params["Y_LABEL"], fontsize=plot_style["Y_LABEL_FONT_SIZE"], rotation=0, labelpad=plot_style["Y_LABELPAD"])

            ax.xaxis.set_major_locator(ticker.MaxNLocator(nbins=plot_style["X_NBINS"]))
            ax.yaxis.set_major_locator(ticker.MaxNLocator(nbins=plot_style["Y_NBINS"]))

            ax.tick_params(axis='x', labelsize=plot_style["TICK_FONTSIZE"])
            ax.tick_params(axis='y', labelsize=plot_style["TICK_FONTSIZE"])

            ax.invert_xaxis()

    for row in range(nrows):
        for col in range(ncols):
            if row >= len(grouped_data[groups[col]]):
                axes[row, col].axis('off')

    plt.tight_layout()

    if path_to_save is not None:
        plt.savefig(path_to_save, dpi=600)

    plt.show()

### `3800-2500` cm$^{-1}$

In [14]:
wn_range = (3800, 2500)

data = data_ranges[wn_range]

print(data.shape)
data.head(3)

(75, 1348)


3799.64885  3798.68447  3797.72009  3796.75571  \
division_1_size_bulk    0.008173    0.006944    0.005343    0.003939   
division_1_size_5       0.016704    0.016252    0.015597    0.014899   
division_1_size_3       0.007885    0.006506    0.004860    0.003460   

                      3795.79134  3794.82696  3793.86258  3792.89820  \
division_1_size_bulk    0.003072    0.002980    0.003841    0.005480   
division_1_size_5       0.014270    0.013765    0.013541    0.013544   
division_1_size_3       0.002667    0.002601    0.003386    0.004675   

                      3791.93382  3790.96945  3790.00507  3789.04069  \
division_1_size_bulk    0.007511    0.009709    0.011900    0.013832   
division_1_size_5       0.013597    0.013683    0.013793    0.013923   
division_1_size_3       0.006086    0.007626    0.009204    0.010741   

                      3788.07631  3787.11194  3786.14756  3785.18318  \
division_1_size_bulk    0.015348    0.016441    0.017239    0.017733   
division_1_size_5       0.014024    0.014010    0.013840    0.013510   
division_1_size_3       0.012031    0.012975    0.013597    0.013761   

                      3784.21880  3783.25442  3782.29005  3781.32567  \
division_1_size_bulk    0.017883    0.018044    0.018444    0.019044   
division_1_size_5       0.013084    0.012645    0.012295    0.012079   
division_1_size_3       0.013601    0.013512    0.013688    0.013979   

                      3780.36129  3779.39691  3778.43253  3777.46816  \
division_1_size_bulk    0.019943    0.021203    0.022851    0.024721   
division_1_size_5       0.011981    0.012027    0.012236    0.012530   
division_1_size_3       0.014457    0.015270    0.016430    0.017805   

                      3776.50378  ...  2523.77691  2522.81253  2521.84816  \
division_1_size_bulk    0.026527  ...    0.047667    0.047085    0.046364   
division_1_size_5       0.012738  ...    0.071707    0.071738    0.071692   
division_1_size_3       0.019006  ...    0.050651    0.050246    0.049691   

                      2520.88378  2519.91940  2518.95502  2517.99065  \
division_1_size_bulk    0.045493    0.044605    0.043762    0.042824   
division_1_size_5       0.071511    0.071224    0.070919    0.070610   
division_1_size_3       0.048967    0.048092    0.047248    0.046508   

                      2517.02627  2516.06189  2515.09751  2514.13313  \
division_1_size_bulk    0.041640    0.040213    0.038663    0.037152   
division_1_size_5       0.070263    0.069870    0.069453    0.069042   
division_1_size_3       0.045735    0.044889    0.044111    0.043450   

                      2513.16876  2512.20438  2511.24000  2510.27562  \
division_1_size_bulk    0.035769    0.034535    0.033435    0.032429   
division_1_size_5       0.068680    0.068369    0.068081    0.067817   
division_1_size_3       0.042814    0.042135    0.041385    0.040664   

                      2509.31124  2508.34687  2507.38249  2506.41811  \
division_1_size_bulk    0.031592    0.031051    0.030593    0.029899   
division_1_size_5       0.067590    0.067435    0.067321    0.067123   
division_1_size_3       0.040074    0.039591    0.039148    0.038560   

                      2505.45373  2504.48935  2503.52498  2502.56060  \
division_1_size_bulk    0.029018    0.027984    0.026712    0.025313   
division_1_size_5       0.066776    0.066312    0.065745    0.065118   
division_1_size_3       0.037730    0.036743    0.035626    0.034448   

                      2501.59622  2500.63184  
division_1_size_bulk    0.023974    0.022884  
division_1_size_5       0.064559    0.064120  
division_1_size_3       0.033422    0.032674  

[3 rows x 1348 columns]

In [15]:
grouped_data = {group: data.loc[samples_description[samples_description["Fraction_grouped_hue"] == group].index] for group in groups}

#### Peaks detection process

In [16]:
prominence = 0.05
height = 0.15
width = 10

In [17]:
peak_data = {}

for group in tqdm(groups):
    group_data = grouped_data[group]

    for sample_id in group_data.index:
        spectrum = group_data.loc[sample_id].values
        wavenumber = group_data.columns.astype(float)

        peak_positions, peak_intensities, _ = find_spectrum_peaks(
            wavenumber=wavenumber,
            spectrum=spectrum,
            prominence=prominence,
            height=height,
            width=width
        )

        peak_data[sample_id] = {
            "positions": peak_positions,
            "intensities": peak_intensities,
            "group": group
        }

100%|████████████████████████████████████████████| 3/3 [00:00<00:00, 164.61it/s]


#### Visualization of spectra with peaks

In [18]:
custom_plot_style = {
    "LINEWIDTH": 3.5,
    "PEAK_SIZE": 64,
    "PEAK_COLOR": "red",
    "TITLE_FONTSIZE": 20,
    "X_LABEL_FONT_SIZE": 16,
    "Y_LABEL_FONT_SIZE": 16,
    "X_LABELPAD": 5,
    "Y_LABELPAD": 15,
    "TICK_FONTSIZE": 14,
    "X_NBINS": 10,
    "Y_NBINS": 12
}

custom_plot_params = {
    "FIGSIZE_SCALE": (6, 3),
    "X_LABEL": 'Волновое число, см$^{-1}$',
    "Y_LABEL": '$A_{n}$'
}

In [19]:
visualize_grouped_spectra(
    grouped_data=grouped_data,
    peak_data=peak_data,
    groups=groups,
    type_color_dict=type_color_dict,
    plot_style=custom_plot_style,
    plot_params=custom_plot_params,
    path_to_save=None
)

3it [00:00, 23.52it/s]


#### Peaks aggregation by posoition

In [20]:
peak_tolerance = 30  # 50
consolidated_peaks = defaultdict(dict)

In [21]:
consolidated_peaks = []

for sample_id, sample_info in peak_data.items():
    positions = sample_info["positions"]
    intensities = sample_info["intensities"]
    
    for pos, intensity in zip(positions, intensities):
        found = False
        
        for cluster in consolidated_peaks:
            if abs(cluster['centroid'] - pos) <= peak_tolerance:
                cluster['samples'][sample_id] = intensity
                cluster['positions'].append(pos)

                cluster['centroid'] = sum(cluster['positions']) / len(cluster['positions'])

                found = True
                break
        if not found:
            consolidated_peaks.append({
                'centroid': pos,
                'positions': [pos],
                'samples': {sample_id: intensity}
            })

In [22]:
columns = sorted([f"$I_{{{round(cluster['centroid'])}}}$" for cluster in consolidated_peaks])
peaks_3800_2500_df = pd.DataFrame(index=peak_data.keys(), columns=columns)

for cluster in consolidated_peaks:
    col_name = f"$I_{{{round(cluster['centroid'])}}}$"
    for sample_id, intensity in cluster['samples'].items():
        peaks_3800_2500_df.at[sample_id, col_name] = intensity

print(peaks_3800_2500_df.shape)
peaks_3800_2500_df.head(3)

(75, 17)


$I_{2559}$ $I_{2930}$ $I_{3006}$ $I_{3067}$ $I_{3102}$  \
division_1_size_2          NaN        1.0        NaN        NaN        NaN   
division_1_size_0.4        NaN        1.0        NaN        NaN        NaN   
division_1_size_0.2        NaN        1.0        NaN        NaN        NaN   

                    $I_{3133}$ $I_{3212}$ $I_{3260}$ $I_{3297}$ $I_{3333}$  \
division_1_size_2          NaN        NaN        NaN   0.802589        NaN   
division_1_size_0.4        NaN        NaN        NaN   0.982932        NaN   
division_1_size_0.2        NaN        NaN        NaN    0.38749        NaN   

                    $I_{3383}$ $I_{3432}$ $I_{3518}$ $I_{3605}$ $I_{3621}$  \
division_1_size_2          NaN        NaN        NaN        NaN        NaN   
division_1_size_0.4        NaN        NaN        NaN        NaN        NaN   
division_1_size_0.2        NaN        NaN        NaN        NaN        NaN   

                    $I_{3733}$ $I_{3760}$  
division_1_size_2      0.21733        NaN  
division_1_size_0.4   0.184752        NaN  
division_1_size_0.2        NaN        NaN

In [23]:
pd.DataFrame(
    peaks_3800_2500_df
    .isna()
    .sum()
).T

$I_{2559}$  $I_{2930}$  $I_{3006}$  $I_{3067}$  $I_{3102}$  $I_{3133}$  \
0          73          30          71          74          74          73   

   $I_{3212}$  $I_{3260}$  $I_{3297}$  $I_{3333}$  $I_{3383}$  $I_{3432}$  \
0          71          73          60          74          34          74   

   $I_{3518}$  $I_{3605}$  $I_{3621}$  $I_{3733}$  $I_{3760}$  
0          72          74          70          64          73

#### Removing features by *NaN-values* count

In [24]:
features_to_drop = peaks_3800_2500_df.columns[peaks_3800_2500_df.isna().mean() >= 0.90].tolist()

print(f'Признаки для исключения:')
for feature in features_to_drop:
    print(f'(*) {feature}')

Признаки для исключения:
(*) $I_{2559}$
(*) $I_{3006}$
(*) $I_{3067}$
(*) $I_{3102}$
(*) $I_{3133}$
(*) $I_{3212}$
(*) $I_{3260}$
(*) $I_{3333}$
(*) $I_{3432}$
(*) $I_{3518}$
(*) $I_{3605}$
(*) $I_{3621}$
(*) $I_{3760}$


In [25]:
peaks_3800_2500_df = peaks_3800_2500_df.drop(columns=features_to_drop)

print(peaks_3800_2500_df.shape)
peaks_3800_2500_df.head(3)

(75, 4)


$I_{2930}$ $I_{3297}$ $I_{3383}$ $I_{3733}$
division_1_size_2          1.0   0.802589        NaN    0.21733
division_1_size_0.4        1.0   0.982932        NaN   0.184752
division_1_size_0.2        1.0    0.38749        NaN        NaN

#### *NaN-values* correction

In [26]:
spectra_data = data_ranges[wn_range].copy()
spectra_data.columns = spectra_data.columns.astype(float)

available_wavenumbers = spectra_data.columns.to_numpy()

for col in peaks_3800_2500_df.columns:
    wn_target = float(col.split('{')[1].split('}')[0])

    nearest_wn = available_wavenumbers[np.argmin(np.abs(available_wavenumbers - wn_target))]

    for sample_id in peaks_3800_2500_df.index:
        if pd.isna(peaks_3800_2500_df.at[sample_id, col]):
            peaks_3800_2500_df.at[sample_id, col] = spectra_data.at[sample_id, nearest_wn]

print(peaks_3800_2500_df.shape)
peaks_3800_2500_df.head(3)

(75, 4)


$I_{2930}$ $I_{3297}$ $I_{3383}$ $I_{3733}$
division_1_size_2          1.0   0.802589   0.634942    0.21733
division_1_size_0.4        1.0   0.982932   0.724401   0.184752
division_1_size_0.2        1.0    0.38749   0.319173   0.101561

*NaN-values analysis*

In [27]:
pd.DataFrame(
    peaks_3800_2500_df
    .isna()
    .sum()
).T

$I_{2930}$  $I_{3297}$  $I_{3383}$  $I_{3733}$
0           0           0           0           0

### `1900-800` cm$^{-1}$

In [28]:
wn_range = (1900, 800)

data = data_ranges[wn_range]

print(data.shape)
data.head(3)

(75, 1141)


1899.82442  1898.86005  1897.89567  1896.93129  \
division_1_size_bulk    0.018023    0.017937    0.017795    0.017695   
division_1_size_5       0.027475    0.027004    0.026550    0.026178   
division_1_size_3       0.034314    0.034232    0.034055    0.033883   

                      1895.96691  1895.00253  1894.03816  1893.07378  \
division_1_size_bulk    0.017644    0.017613    0.017604    0.017598   
division_1_size_5       0.025881    0.025605    0.025365    0.025128   
division_1_size_3       0.033750    0.033608    0.033482    0.033354   

                      1892.10940  1891.14502  1890.18065  1889.21627  \
division_1_size_bulk    0.017658     0.01781    0.018026    0.018247   
division_1_size_5       0.024864     0.02456    0.024223    0.023874   
division_1_size_3       0.033236     0.03318    0.033235    0.033333   

                      1888.25189  1887.28751  1886.32313  1885.35876  \
division_1_size_bulk    0.018432    0.018651    0.018987    0.019459   
division_1_size_5       0.023498    0.023129    0.022806    0.022544   
division_1_size_3       0.033344    0.033302    0.033269    0.033255   

                      1884.39438  1883.43000  1882.46562  1881.50124  \
division_1_size_bulk    0.020012    0.020615    0.021318    0.022129   
division_1_size_5       0.022345    0.022199    0.022120    0.022087   
division_1_size_3       0.033261    0.033321    0.033499    0.033782   

                      1880.53687  1879.57249  1878.60811  1877.64373  \
division_1_size_bulk    0.023031    0.023996    0.024981    0.025936   
division_1_size_5       0.022079    0.022101    0.022153    0.022220   
division_1_size_3       0.034174    0.034706    0.035356    0.036033   

                      1876.67935  ...  823.57871   822.61433   821.64995   \
division_1_size_bulk    0.026837  ...    0.029586    0.028214    0.026986   
division_1_size_5       0.022256  ...    0.026956    0.025571    0.024368   
division_1_size_3       0.036628  ...    0.040132    0.038134    0.036383   

                      820.68558   819.72120   818.75682   817.79244   \
division_1_size_bulk    0.025897    0.024897    0.023993    0.023181   
division_1_size_5       0.023359    0.022495    0.021711    0.020943   
division_1_size_3       0.034818    0.033321    0.031832    0.030401   

                      816.82806   815.86369   814.89931   813.93493   \
division_1_size_bulk    0.022394    0.021538    0.020497    0.019275   
division_1_size_5       0.020128    0.019282    0.018375    0.017313   
division_1_size_3       0.029016    0.027610    0.026115    0.024499   

                      812.97055   812.00618   811.04180   810.07742   \
division_1_size_bulk    0.017951    0.016505    0.014823    0.012940   
division_1_size_5       0.016045    0.014623    0.013125    0.011586   
division_1_size_3       0.022817    0.021116    0.019349    0.017454   

                      809.11304   808.14866   807.18429   806.21991   \
division_1_size_bulk    0.010974    0.009058    0.007383    0.005972   
division_1_size_5       0.010015    0.008464    0.007005    0.005644   
division_1_size_3       0.015411    0.013298    0.011293    0.009414   

                      805.25553   804.29115   803.32677   802.36240   \
division_1_size_bulk    0.004751    0.003661    0.002658    0.001765   
division_1_size_5       0.004394    0.003317    0.002400    0.001567   
division_1_size_3       0.007591    0.005859    0.004230    0.002681   

                      801.39802   800.43364   
division_1_size_bulk    0.000955         0.0  
division_1_size_5       0.000781         0.0  
division_1_size_3       0.001290         0.0  

[3 rows x 1141 columns]

In [29]:
grouped_data = {group: data.loc[samples_description[samples_description["Fraction_grouped_hue"] == group].index] for group in groups}

#### Peaks detection process

In [30]:
prominence = 0.05
height = 0.15
width = 10

In [31]:
peak_data = {}

for col, group in tqdm(enumerate(groups)):
    group_data = grouped_data[group]

    for sample_id in group_data.index:
        spectrum = group_data.loc[sample_id].values
        wavenumber = group_data.columns.astype(float)

        peak_positions, peak_intensities, _ = find_spectrum_peaks(
            wavenumber=wavenumber,
            spectrum=spectrum,
            prominence=prominence,
            height=height,
            width=width
        )

        peak_data[sample_id] = {
            "positions": peak_positions,
            "intensities": peak_intensities,
            "group": group
        }

3it [00:00, 398.46it/s]


#### Spectra with peaks visualization

In [32]:
custom_plot_style = {
    "LINEWIDTH": 3.5,
    "PEAK_SIZE": 64,
    "PEAK_COLOR": "red",
    "TITLE_FONTSIZE": 20,
    "X_LABEL_FONT_SIZE": 16,
    "Y_LABEL_FONT_SIZE": 16,
    "X_LABELPAD": 5,
    "Y_LABELPAD": 15,
    "TICK_FONTSIZE": 14,
    "X_NBINS": 10,
    "Y_NBINS": 12
}

custom_plot_params = {
    "FIGSIZE_SCALE": (6, 3),
    "X_LABEL": 'Волновое число, см$^{-1}$',
    "Y_LABEL": '$A_{n}$'
}

In [ ]:
visualize_grouped_spectra(
    grouped_data=grouped_data,
    peak_data=peak_data,
    groups=groups,
    type_color_dict=type_color_dict,
    plot_style=custom_plot_style,
    plot_params=custom_plot_params,
    path_to_save=None
)

2it [00:00, 14.04it/s]

#### Peaks aggregation by position

In [ ]:
peak_tolerance = 30
consolidated_peaks = defaultdict(dict)

In [ ]:
consolidated_peaks = []

for sample_id, sample_info in peak_data.items():
    positions = sample_info["positions"]
    intensities = sample_info["intensities"]
    
    for pos, intensity in zip(positions, intensities):
        found = False
        
        for cluster in consolidated_peaks:
            if abs(cluster['centroid'] - pos) <= peak_tolerance:
                cluster['samples'][sample_id] = intensity
                cluster['positions'].append(pos)

                cluster['centroid'] = sum(cluster['positions']) / len(cluster['positions'])

                found = True
                break
        if not found:
            consolidated_peaks.append({
                'centroid': pos,
                'positions': [pos],
                'samples': {sample_id: intensity}
            })

In [ ]:
columns = sorted([f"$I_{{{round(cluster['centroid'])}}}$" for cluster in consolidated_peaks])
peaks_1900_800_df = pd.DataFrame(index=peak_data.keys(), columns=columns)

for cluster in consolidated_peaks:
    col_name = f"$I_{{{round(cluster['centroid'])}}}$"
    for sample_id, intensity in cluster['samples'].items():
        peaks_1900_800_df.at[sample_id, col_name] = intensity

print(peaks_1900_800_df.shape)
peaks_1900_800_df.head(3)

In [ ]:
pd.DataFrame(
    peaks_1900_800_df
    .isna()
    .sum()
).T

#### Removing features by *NaN-values* count

In [ ]:
features_to_drop = peaks_1900_800_df.columns[peaks_1900_800_df.isna().mean() >= 0.90].tolist()

print(f'Признаки для исключения:')
for feature in features_to_drop:
    print(f'(*) {feature}')

In [ ]:
peaks_1900_800_df = peaks_1900_800_df.drop(columns=features_to_drop)

print(peaks_1900_800_df.shape)
peaks_1900_800_df.head(3)

#### *NaN-values* correction

In [ ]:
spectra_data = data_ranges[wn_range].copy()
spectra_data.columns = spectra_data.columns.astype(float)

available_wavenumbers = spectra_data.columns.to_numpy()

for col in peaks_1900_800_df.columns:
    wn_target = float(col.split('{')[1].split('}')[0])

    nearest_wn = available_wavenumbers[np.argmin(np.abs(available_wavenumbers - wn_target))]

    for sample_id in peaks_1900_800_df.index:
        if pd.isna(peaks_1900_800_df.at[sample_id, col]):
            peaks_1900_800_df.at[sample_id, col] = spectra_data.at[sample_id, nearest_wn]

print(peaks_1900_800_df.shape)
peaks_1900_800_df.head(3)

*NaN-values analysis*

In [ ]:
pd.DataFrame(
    peaks_1900_800_df
    .isna()
    .sum()
).T

#### Sorting by index

In [ ]:
peaks_1900_800_df = peaks_1900_800_df.sort_index(
    key=lambda x: x.map(lambda y: (float(y.split('_')[1]), -float(y.split('_')[-1].replace('bulk', '1000')))),
    ascending=True
)

print(peaks_1900_800_df.shape)
peaks_1900_800_df.head(3)

### Merging aggregated data

In [ ]:
print(
    f'(*) 3800-2500: {peaks_3800_2500_df.shape}',
    f'(*) 1900-800: {peaks_3800_2500_df.shape}',
    sep='\n'
)

In [ ]:
peaks_3800_2500_1900_800_df = pd.merge(
    left=peaks_3800_2500_df,
    right=peaks_1900_800_df,
    left_index=True,
    right_index=True,
    how='inner'
)

print(peaks_3800_2500_1900_800_df.shape)
peaks_3800_2500_1900_800_df.head(3)

#### Sorting by index

In [ ]:
peaks_3800_2500_1900_800_df = peaks_3800_2500_1900_800_df.sort_index(
    key=lambda x: x.map(lambda y: (float(y.split('_')[1]), -float(y.split('_')[-1].replace('bulk', '1000')))),
    ascending=True
)

print(peaks_3800_2500_1900_800_df.shape)
peaks_3800_2500_1900_800_df.head(3)

#### Sorting by column

In [ ]:
wavenumbers = {col: int(col.split('{')[1].split('}')[0]) for col in peaks_3800_2500_1900_800_df.columns}

sorted_columns = sorted(wavenumbers, key=wavenumbers.get, reverse=True)

peaks_3800_2500_1900_800_df = peaks_3800_2500_1900_800_df[sorted_columns]

print(peaks_3800_2500_1900_800_df.shape)
peaks_3800_2500_1900_800_df.head(3)

*Analysis of unique peaks*

In [ ]:
unique_peak_positions = [int(peak.split('{')[1].split('}')[0]) for peak in peaks_3800_2500_1900_800_df.columns.tolist()]

print(unique_peak_positions)

## Integral intensity of spectral ranges extraction

### Function for features calculation

In [ ]:
def compute_interval_and_peak_region_features(spectra_data, peaks_df, intervals, windows=(25, 50)):
    df = pd.DataFrame(index=spectra_data.index)
    wn = spectra_data.columns.astype(float)

    for a, b in intervals:
        low, high = min(a, b), max(a, b)

        # Mean intensity in intervals
        mean_name = f"$\\overline{{I}}_{{{high}\\text{{–}}{low}}}$"
        mask = (wn >= low) & (wn <= high)
        df[mean_name] = spectra_data.loc[:, mask].mean(axis=1)

        # Sum of intensities of peaks in intervals — using Σ
        sum_name = f"$\\Sigma I_{{p,\\ {high}\\text{{–}}{low}}}$"
        selected_cols = [
            col for col in peaks_df.columns
            if col.startswith("$I_{") and low <= int(col.split('{')[1].split('}')[0]) <= high
        ]
        df[sum_name] = peaks_df[selected_cols].sum(axis=1)

    # Sum of peaks in range of peak maximum ± window
    for sample_id in spectra_data.index:
        row = peaks_df.loc[sample_id].dropna()
        for col in row.index:
            if col.startswith("$I_{"):
                try:
                    center = int(col.split('{')[1].split('}')[0])
                except ValueError:
                    continue

                for w in windows:
                    left, right = center - w, center + w
                    mask = (wn >= left) & (wn <= right)
                    if mask.any():
                        region_mean = spectra_data.loc[sample_id, wn[mask]].mean()
                        feat_name = f"$\\overline{{I}}_{{{center} \\pm {w}}}$"
                        df.at[sample_id, feat_name] = region_mean

    return df

### `3800-2500`

In [ ]:
intervals_3800_2500 = [(3800, 2500)]

In [ ]:
interval_features_3800_2500_df = compute_interval_and_peak_region_features(
    spectra_data=data_ranges[(3800, 2500)],
    peaks_df=peaks_3800_2500_df,
    intervals=intervals_3800_2500,
    windows=(32, )
)

print(interval_features_3800_2500_df.shape)
interval_features_3800_2500_df.head(3)

### `1900-800`

In [ ]:
intervals_1900_800 = [(1800, 900), (1800, 1500), (1500, 1300), (1300, 900)]

In [ ]:
interval_features_1900_800_df = compute_interval_and_peak_region_features(
    spectra_data=data_ranges[(1900, 800)],
    peaks_df=peaks_1900_800_df,
    intervals=intervals_1900_800,
    windows=(32, )
)

print(interval_features_1900_800_df.shape)
interval_features_1900_800_df.head(3)

### Merging datasets

In [ ]:
print(
    f'(*) 3800-2500: {interval_features_3800_2500_df.shape}',
    f'(*) 1900-800: {interval_features_1900_800_df.shape}',
    sep='\n'
)

In [ ]:
interval_features_3800_2500_1900_800_df = pd.merge(
    left=interval_features_3800_2500_df,
    right=interval_features_1900_800_df,
    left_index=True,
    right_index=True,
    how='inner'
)

print(interval_features_3800_2500_1900_800_df.shape)
interval_features_3800_2500_1900_800_df.head(3)

In [ ]:
interval_features_3800_2500_1900_800_df = interval_features_3800_2500_1900_800_df.sort_index(
    key=lambda x: x.map(lambda y: (float(y.split('_')[1]), -float(y.split('_')[-1].replace('bulk', '1000')))),
    ascending=True
)

print(interval_features_3800_2500_1900_800_df.shape)
interval_features_3800_2500_1900_800_df.head(3)

*NaN-values analysis*

In [ ]:
pd.DataFrame(
    interval_features_3800_2500_1900_800_df
    .isna()
    .sum()
).T

## Final dataset construction

In [ ]:
features_df = pd.merge(
    left=peaks_3800_2500_1900_800_df,
    right=interval_features_3800_2500_1900_800_df,
    left_index=True,
    right_index=True,
    how='inner'
)

print(features_df.shape)
features_df.head(3)

### Sorting by index

In [ ]:
features_df = features_df.sort_index(
    key=lambda x: x.map(lambda y: (float(y.split('_')[1]), -float(y.split('_')[-1].replace('bulk', '1000')))),
    ascending=True
)

print(features_df.shape)
features_df.head(3)

### Sorting by column

In [ ]:
def extract_wavenumber(col):
    match = re.search(r'\{(\d+)', col)
    return int(match.group(1)) if match else float('-inf')

In [ ]:
col2wn = {col: extract_wavenumber(col) for col in features_df.columns}

sorted_columns = sorted(col2wn, key=col2wn.get, reverse=True)

features_df = features_df[sorted_columns]

print(features_df.shape)
features_df.head(3)

# Saving data

In [ ]:
path_to_save = './../data/processed_data'

In [ ]:
features_df.to_csv(f'{path_to_save}/ftir_extracted_features.csv', sep=';')